## Exercice 1

L'idée était de vous faire mettre en forme un jeu de données vous-même, avant d'effectuer une ACP. En effet l'ACP directe n'est pas possible car il y a trop de lignes incomplètes, des colonnes a priori peu pertinentes, et des données de type séries temporelles (que l'on ramènera à une seule valeur).

In [ ]:
# Import du jeu de données brut
data <- read.csv("https://raw.githubusercontent.com/owid/covid-19-data/master/public/data/owid-covid-data.csv")

In [ ]:
# Affichage d'un aperçu du jeu de données ; fonctions head() et summary() = bons réflexes :)
dim(data)
head(data)

In [ ]:
# On ne verra pas de méthodes s'appliquant sur des séries temporelles dans ce cours,
# donc on se limite ici à des statistiques globales prises au dernier jour :
dmax <- max(data$date) #28/11/2021 aujourd'hui, 29/11 demain etc...
data <- data[data$date == dmax,] #filtre sur les lignes, donc *avant* la virgule
dim(data)
summary(data)

In [ ]:
# Le jeu de données comprend quelques "lignes résumé" (continents, catégories de revenus...).
# En observant un peu, on remarque que leur code ISO démarre par "OWID_" :
owid_lines <- startsWith(data$iso_code, "OWID_")
data[owid_lines,]

In [ ]:
# Hormis le Kosovo, les autres lignes sont à supprimer car on retrouvera ces indicateurs (et plus encore)
# via l'analyse ACP. Renommons aussi OWID_KOS après avoir vérifier que ce code n'est pas utilisé :
any(data$iso_code == "KOS")
kosovo_index = which(data$iso_code == "OWID_KOS")
data[kosovo_index, "iso_code"] <- "KOS"

In [ ]:
# Supprimons alors les lignes "aggrégées" :
owid_lines <- startsWith(data$iso_code, "OWID_")
data <- data[!owid_lines,]
dim(data)

In [ ]:
# Pour supprimer les lignes avec valeurs manquantes, il y a plusieurs options.
# J'en indique ici 3, de la plus complexe à la plus simple :
data1 <- data[apply(data, 1, function(row) all(!is.na(row))),] #méthode 1
data2 <- data[complete.cases(data),]                           #méthode 2
data3 <- na.omit(data)                                         #méthode 3

In [ ]:
# On remarque alors qu'il n'y a plus aucune ligne ==> il faut restreindre les colonnes
# (ou "deviner" les valeurs manquantes d'une manière ou d'une autre : voir le package missMDA)
# (ici on se contente de la version simple : pas de données manquantes en entrée).
nrow(data3)

In [ ]:
# Que représentent les variables ?
colnames(data)

In [ ]:
# Variables "new_*" : instantané journalier d'un certain indicateur. On ne s'y intéressera pas ici (cf. plus bas).
# De même pour les variables "weekly_*" (indicateurs hebdomadaires, j'imagine). Reste :
selection <- colnames(data)[!startsWith(colnames(data), "new_") & !startsWith(colnames(data), "weekly_")]

In [ ]:
# Colonnes avec +50% de valeurs renseignées
selection <- selection[ apply(data[,selection], 2, function(col) sum(!is.na(col)) > nrow(data)/2) ]
selection

On y voit enfin plus clair :

- iso_code : identifiant d'un pays, sur 3 lettres
- location : nom du pays
- continent, date : heu, continent, et date =)
- total_cases : nombre total de cas enregistrés jusqu'à dmax
- total_deaths : nombre total de décès enregistrés jusqu'à dmax
- total_cases_per_million : nombre relatif de cas totaux (par million)
- total_deaths_per_million : nombre relatif de décès (par million)
- tests_units : "Units used by the location to report its testing data" https://github.com/owid/covid-19-data/blob/master/public/data/README.md <br> en fait cette colonne ne contient que ". " ==> inutilisable.
- population : nombre d'habitants
- population_density : densité de population (par kilomètre carré)
- median_age : âge médian, 50% des gens sont plus jeunes et 50% plus vieux
- aged_65_older : pourcentage de personnes dépassant 65 ans
- aged_70_older : pareil avec 70 ans
- gdp_per_capita : PIB par habitant
- extreme_poverty : pourcentage de la population sous le seuil d'extrême pauvreté
- cardiovasc_death_rate : "Death rate from cardiovascular disease in 2017 (annual number of deaths per 100,000 people)"
- diabetes_prevalence : Diabetes prevalence (% of population aged 20 to 79) in 2017
- female_smokers : pourcentage de fumeuses
- male_smokers : pourcentage de fumeurs
- hospital_beds_per_thousand : nombre de lits d'hôpital par tranche de 1000 habitants
- life_expectancy : espérance de vie
- human_development_index : indice de développement humain

In [ ]:
data$tests_units #???

In [ ]:
selection <- selection[selection != "tests_units"]
newData <- na.omit(data[,selection])
nrow(newData)

92 lignes est raisonnable (proche de 50% de la taille du jeu de données initial).
Cependant, pour être cohérent il faut en plus choisir un type de variable : absolu, ou relatif ? Je préfère les indicateurs relatifs (\*\_per\_million, \*\_density) :

In [ ]:
selection <- selection[!selection %in% c("total_cases", "total_deaths", "population")]
newData <- na.omit(data[,selection])
nrow(newData) #92 encore

In [ ]:
rownames(newData) <- newData$iso_code #pour l'affichage des individus
newData <- newData[,-c(1,4)] #suppression des colonnes "code ISO" et "date", désormais inutiles

**Note :** toute l'analyse jusqu'ici aurait pu se faire aussi facilement avec un autre langage, Python par exemple. <br>
À partir d'ici cependant, le package R FactoMineR est très pratique (pas d'équivalent Python (?!))

In [ ]:
# ...On est enfin prêt pour l'ACP !
library(FactoMineR)
res.pca <- PCA(newData, quali.sup=1:2, ncp=6, graph=FALSE)

In [ ]:
options(repr.plot.width=15, repr.plot.height=10)
plotInd <- plot(res.pca, choix="ind", invisible="quali")
plotVar <- plot(res.pca, choix="var")
library(gridExtra)
grid.arrange(plotInd, plotVar, ncol=2)

Bon, il semble qu'aucun individu ne se détache. En fait certaines lignes ont presque toutes leurs valeurs renseignées, et une fois complétées à l'aide de Google on trouve des individus extrêmes (Monaco, Singapour).

In [ ]:
which(data$location %in% c("Monaco", "Singapore"))

In [ ]:
data[158,selection]

Côté variables, aged_65_older et aged_70_older apparaissent très corrélées (en fait même confondues). C'est logique, on gardera donc seulement aged_70_older après vérification numérique :

In [ ]:
cor(newData[,c("aged_65_older", "aged_70_older")])

In [ ]:
newData <- subset(newData, select=-aged_65_older)

In [ ]:
res.pca <- PCA(newData, quali.sup=1:2, ncp=6, graph=FALSE)

In [ ]:
plotInd <- plot(res.pca, choix="ind", invisible="quali", habillage=1)
plotVar <- plot(res.pca, choix="var")
library(gridExtra)
grid.arrange(plotInd, plotVar, ncol=2)

Environ 65% de l'inertie expliquée dans ce premier plan ACP (49.3 + 14.2). Le cercle des corrélations oppose logiquement "richesse" à droite (HDI, PIB/hab), avec "pauvreté" à gauche. Sur le nuage des individus cela correspond grossièrement à l'opposition Europe occidentale / Afrique (quelques exceptions : Tunisie, Seychelles, ...).

Il est intéressant de constater que les indicateurs de richesse sont très corrélés positivement au nombre de morts par millions, lui-même anti-corrélé avec extreme_poverty : le COVID frapperait plutôt les riches ? Mais pourquoi donc, puisque le virus est partout ? Et bien un élément de réponse se trouve dans ce même plan ACP : aged_70_older => on y vit plus vieux, et dans une moindre mesure diabetes_prevalence => plus de cas de diabète (à vérifier numériquement).

In [ ]:
cor(newData[,c("aged_70_older", "total_deaths_per_million", "human_development_index",
               "diabetes_prevalence", "extreme_poverty")])

La corrélation (resp. anti-corrélation) aged_70_older avec HDI (resp. extreme_poverty) et total_deaths est vérifiée. De même, on observe une légère corrélation positive (resp. négative) entre diabetes_prevalence et HDI (resp. extreme_poverty).

Ensuite, le taux de fumeuses semble très corrélé à l'âge médian : les femmes auraient plus tendance à fumer dans les pays où l'on vit plus vieux (donc en général plus riches). Ce n'est pas le cas de male_smokers : le taux de fumeurs n'indique quant à lui pas grand chose. De même, et plus étonnament, le taux de mortalité par maladies cardiovasculaires (infarctus j'imagine) ne paraît corrélé à rien - si ce n'est justement et assez logiquement, la proportion de fumeurs : "According to the American Heart Association, cardiovascular disease accounts for about 800,000 U.S. deaths every year,5 making it the leading cause of all deaths in the United States. Of those, nearly 20 percent are due to cigarette smoking." [https://www.fda.gov/tobacco-products/health-effects-tobacco-use/how-smoking-affects-heart-health#]

La coloration par continents montre une opposition haut/bas entre Europe de l'est et Europe de l'ouest + USA/Canada/Israel/Corée/Australie. Il semble y avoir relativement plus de fumeurs en Géorgie/Ukraine/Russie. les pays d'Amérique centrale et du sud sont plus bas, donc a priori moins touchés par les décès par infarctus et comportant moins de fumeurs. Il n'y a pas assez de pays d'Océanie pour en dire grand chose, et l'Asie est répartie un peu partout, montrant une grande inhomogénéité en comparaison aux autres continents.

Vérifions notre analyse en regardant de plus près quelques individus :

In [ ]:
indivs_indices <- rownames(newData) %in% c("LUX", "UKR", "NER", "ECU")
newData[indivs_indices,c("location", "total_deaths_per_million", "aged_70_older", "male_smokers",
                         "cardiovasc_death_rate", "human_development_index")]

Luxembourg : population âgée, HDI élevé, 2x moins de fumeurs qu'en Ukraine mais 2x + qu'en Equateur. <br>
Niger : population jeune, HDI bas, peu de fumeurs, très peu de morts du COVID.

Bref, passons au second plan ACP :

In [ ]:
plotInd <- plot(res.pca, choix="ind", invisible="quali", habillage=1, axes=3:4)
plotVar <- plot(res.pca, choix="var", axes=3:4)
library(gridExtra)
grid.arrange(plotInd, plotVar, ncol=2)

Peu d'inertie expliquée dans ce plan (à peine 18%), mais une observation intéressante : anti-corrélation population_density et total_deaths_per_million ? À vérifier numériquement bien sûr car cette dernière flèche est loin du bord. Ce serait cependant cohérent : densément peuplé => contaminations plus faciles => plus de cas => plus de personnes très fragiles touchées => plus de morts.

On note aussi l'anti-corrélation entre diabetes_prevalence et extreme_poverty, déjà un peu observée dans le premier plan. Vérification numérique :

In [ ]:
indivs_indices <- rownames(newData) %in% c("MLT", "EGY", "MNE", "MWI")
newData[indivs_indices,c("location", "total_deaths_per_million", "population_density",
                         "diabetes_prevalence", "extreme_poverty")]

Opposition Égypte / malawi vérifiée sur l'axe diabète/pauvreté, ainsi que malte/Montenegro sur l'axe morts_par_million/densité.

## Exercice 2

À l'URL indiquée, on lit clairement ce que représente chaque variable :

1. cap-shape: bell=b,conical=c,convex=x,flat=f, knobbed=k,sunken=s
2. cap-surface: fibrous=f,grooves=g,scaly=y,smooth=s
3. cap-color: brown=n,buff=b,cinnamon=c,gray=g,green=r, pink=p,purple=u,red=e,white=w,yellow=y
4. bruises?: bruises=t,no=f
5. odor: almond=a,anise=l,creosote=c,fishy=y,foul=f, musty=m,none=n,pungent=p,spicy=s
6. gill-attachment: attached=a,descending=d,free=f,notched=n
7. gill-spacing: close=c,crowded=w,distant=d
8. gill-size: broad=b,narrow=n
9. gill-color: black=k,brown=n,buff=b,chocolate=h,gray=g, green=r,orange=o,pink=p,purple=u,red=e, white=w,yellow=y
10. stalk-shape: enlarging=e,tapering=t
11. stalk-root: bulbous=b,club=c,cup=u,equal=e, rhizomorphs=z,rooted=r,missing=?
12. stalk-surface-above-ring: fibrous=f,scaly=y,silky=k,smooth=s
13. stalk-surface-below-ring: fibrous=f,scaly=y,silky=k,smooth=s
14. stalk-color-above-ring: brown=n,buff=b,cinnamon=c,gray=g,orange=o, pink=p,red=e,white=w,yellow=y
15. stalk-color-below-ring: brown=n,buff=b,cinnamon=c,gray=g,orange=o, pink=p,red=e,white=w,yellow=y
16. veil-type: partial=p,universal=u
17. veil-color: brown=n,orange=o,white=w,yellow=y
18. ring-number: none=n,one=o,two=t
19. ring-type: cobwebby=c,evanescent=e,flaring=f,large=l, none=n,pendant=p,sheathing=s,zone=z
20. spore-print-color: black=k,brown=n,buff=b,chocolate=h,green=r, orange=o,purple=u,white=w,yellow=y
21. population: abundant=a,clustered=c,numerous=n, scattered=s,several=v,solitary=y
22. habitat: grasses=g,leaves=l,meadows=m,paths=p, urban=u,waste=w,woods=d

Note : gill = branchie, stalk = tige, veil = voile (merci Google Translate).

In [ ]:
# Récupération du jeu de données
data <- read.csv("https://archive.ics.uci.edu/ml/machine-learning-databases/mushroom/agaricus-lepiota.data",
                 header=FALSE) #attention: pas de header (on s'en rend vite compte)
dim(data)
head(data)

23 variables : la première indique si le champignon est comestible (edible) ou non (poisonous).

On peut se poser diverses questions passionnantes sur les correspondances entre modalités, par exemple :

- l'odeur d'un champignon est-elle corrélée à son habitat ?
- un champignon de couleur verte a-t-il tendance à être empoisonné ?
- la couleur des branchies est-elle liée à celle de la tige ?
- ...etc

In [ ]:
# Commençons par donner des noms aux colonnes :
colnames(data) <- c("edible", "cap-shape", "cap-surface", "cap-color", "bruises", "odor", "gill-attachment",
                    "gill-spacing", "gill-size", "gill-color", "stalk-shape", "stalk-root",
                    "stalk-surface-above-ring", "stalk-surface-below-ring", "stalk-color-above-ring",
                    "stalk-color-below-ring", "veil-type", "veil-color", "ring-number", "ring-type",
                    "spore-print-color", "population", "habitat")

In [ ]:
# Essayons odeur / habitat :
eff_obs <- table(subset(data, select=c("odor", "habitat")))
eff_obs

Certaines lignes sont identiques : odeurs a/l et s/y + m/c (proportionnelles : c'est pareil). Elles peuvent d'ailleurs être regroupées sans changer le résultat de l'analyse : faisons ça.

In [ ]:
eff_obs[1,] <- 2 * eff_obs[1,]
eff_obs[2,] <- eff_obs[2,] + eff_obs[5,]
eff_obs[8,] <- 2 * eff_obs[8,]
rownames(eff_obs)[c(1,2,8)] <- c("a-l", "c-m", "s-y")
eff_obs <- eff_obs[c(1:3, 6:8),]
eff_obs

In [ ]:
# Effectifs théoriques, pour comparaison :
eff_theo <- as.matrix(rowSums(eff_obs)) %*% colSums(eff_obs) / sum(eff_obs)
colnames(eff_theo) <- colnames(eff_obs)
round(eff_theo)

In [ ]:
res.ca <- CA(eff_obs, graph=FALSE)
plot(res.ca)

a-l (odeur) et m (habitat) sont du même côté : les prés contiennent surtout des champignons qui sentent l'amande ou l'anis (le tableau numérique - effectifs observés - indique qu'il faut lire l'association ainsi ; on peut aussi s'aider des effectifs théoriques : "m" est significativement plus associé avec a-l qu'en cas d'indépendance).

f, s-y sont du même côté que l et p : les champignons d'odeur "foul", "spicy" et "fishy" (épicé, nauséabond, poisson : bref des champis qu'on n'a pas très envie de manger a priori) se trouvent significativement plus dans les feuilles et sur les chemins, en comparaison aux effectifs théoriques. Pourquoi, ne me demandez pas.

p (odeur) / u (habitat) semble ressortir : odeur âcre (merci G...) en milieu urbain. On n'aurait pas très envie de manger des champignons poussant au milieu du béton, donc disons que c'est conforme à l'intuition.

Enfin, reste n/w (odeur/habitat) et c-m/d : champignons inodore dans les déchets (heu... ? admettons ^^), et champis sentant la "créosote" (charbon ? ...apparemment c'est un mot français) et le moisi dans les bois : assez cohérent disons.

J'ai un peu la flemme d'écrire autant de détails pour les deux autres cas, alors j'irai à l'essentiel :

In [ ]:
eff_obs <- table(subset(data, select=c("cap-color", "edible")))
eff_obs
eff_theo <- as.matrix(rowSums(eff_obs)) %*% colSums(eff_obs) / sum(eff_obs)
colnames(eff_theo) <- colnames(eff_obs)
round(eff_theo)
res.ca <- CA(eff_obs, graph=FALSE)
#plot(res.ca) #erreur: seulement deux modalités => unidimensionnel
              #                                 => "plot" manuel.. (?!)
xrange <- range(res.ca$row$coord, res.ca$col$coord)
plot(NULL, xlim=xrange, ylim=c(-1,1))
points(res.ca$row$coord, rep(0, length(res.ca$row$coord)), col="blue", pch=19, cex=2)
points(res.ca$col$coord, rep(0, length(res.ca$col$coord)), col="red", pch=19, cex=2)
text(res.ca$row$coord, rep(-0.2, length(res.ca$row$coord)), rownames(eff_obs), col="blue", cex=2)
text(res.ca$col$coord, rep(0.2, length(res.ca$col$coord)), colnames(eff_obs), col="red", cex=2)

b, y, p, e : plutôt poison - jaune/rouge/rose/"chamois" <br>
n, g : on sait pas trop, faire attention - marron/gris <br>
w, c : plutôt comestibles (3 chances sur 4 disons) - blanc/"cannelle" (heu... cannelle != marron ?! c'est subtil !) <br>
r, u : tout est bon ! - vert/pourpre

Ok pour jaune/rouge/rose = méfiance, mais à part ça, je n'avais aucune intuition sur le sujet et cette étude ne m'inspirera pas spécialement confiance en présence d'un champignon violet =)

Note : deux lignes identiques, r = u.

Finalement, couleur des branchies vs. couleur de la tige "sous anneau" (c'est précis !) ?

In [ ]:
eff_obs <- table(subset(data, select=c("gill-color", "stalk-color-below-ring")))
eff_obs
eff_theo <- as.matrix(rowSums(eff_obs)) %*% colSums(eff_obs) / sum(eff_obs)
colnames(eff_theo) <- colnames(eff_obs)
round(eff_theo)
res.ca <- CA(eff_obs, graph=FALSE)
plot(res.ca)

e/e : rouge/rouge. Ok. <br>
y/o : jaune (branchies) / orange (tige). Ok, c'est assorti. <br>
o/c : orange (branchies) / cannelle (tige). De même, ce n'est pas choquant.

Le reste est proche de l'indépendance d'après le graphe.